# Copying Adam Taylor's PCam5c driver to python top layer

In [1]:
from pynq import Overlay
from kv260 import BaseOverlay
from pynq.lib.iic import AxiIIC 
from pynq.lib.video import *
import numpy as np
from time import sleep
import PIL.Image

import periphery 
from periphery import MMIO

adams = Overlay("modified_taylor_bits/taylor_v3.bit", ignore_version=True)
#base = BaseOverlay("base.bit")

In [2]:
'''Instantiating a branch of the Default IP Class (overlay.py file) for each ip '''

vdma = adams.axi_vdma_0
demosaic = adams.v_demosaic_0
gamma = adams.v_gamma_lut_0

In [3]:
'''Extracting base address and size/length of memory region from the Default_IP class '''
gamma_base_addr = gamma.mmio.base_addr
gamma_size = gamma.mmio.length

'''Intanstiating the new periphery.mmio class by feeding it the base address and size of memory allocation for gamma IP, as extracted from previous class '''
periphery = MMIO(gamma_base_addr, gamma_size)

print(periphery.size)

def gamma_calc(gamma_val):
    gamma_reg = []
    i = 0
    for i in range(0,256):
        gamma_reg.append( 256*(i/256)**(1/gamma_val) )
    return gamma_reg

def count_loop(offset, gamma_corr):
    count= 0 
    while count < 0x200:
        periphery.write16(offset + count, int(count/2))
        print(count)
        count = count + 2

65536


In [4]:
def demosaic_config(width, height):
    demosaic.write(0x10, width)
    demosaic.write(0x18, height)
    demosaic.write(0x28, 0x00)
    
    d_read = demosaic.read(0x00)
    print(hex(d_read))
    
    demosaic.write(0x00,0x81)
    
    d_read = demosaic.read(0x00)
    print(hex(d_read))
    return 

In [40]:
def gamma_config(width, height):
    gamma.write(0x10, width)
    gamma.write(0x18, height)
    gamma.write(0x20, 0x00)
    
    gamma_reg = gamma_calc(1.3)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x800 + i, int(gamma_reg[int(i/2)]))
        
    gamma_reg = gamma_calc(1.3)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x1000 + i, int(gamma_reg[int(i/2)])) 
        
    gamma_reg = gamma_calc(1.3)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x1800 + i, int(gamma_reg[int(i/2)]))

    gamma.write(0x00, 0x81)
    #gamma.read(0x00)
    return 

In [41]:
iic = adams.axi_iic_0

iic_cam_addr = 0x3c
sw_iic_addr = 0x74
rx_data = bytes(10)
tx_data = [0,0,0,0,0,0]

In [42]:
def setup_i2c_switch():
    tx_data[0] = 0x04
    iic.send(sw_iic_addr, tx_data, 1)               

In [43]:
def detect_camera():
    tx_data[0] = 0x31;  tx_data[1] = 0x00;

    iic.send(iic_cam_addr, tx_data, 2)        
    print('send complete')
    sleep(0.5)
    
    status = iic.receive(iic_cam_addr, rx_data, 1)
    if hex(rx_data[0]) != '0x78':
        print("camera not detected")
        print(rx_data)        
    else:
        print("camera detected")            

In [44]:
def reset_camera(cfg):   
    tx_data[0] = 0x30; tx_data[1] = 0x08; tx_data[2] = cfg;
    
    iic.send(iic_cam_addr, tx_data, 3)          

In [45]:
def camera_chip_id_low():   
    tx_data[0] = 0x30;  tx_data[1] = 0x0A;

    iic.send(iic_cam_addr, tx_data, 2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x56':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [46]:
def camera_chip_id_high():    
    tx_data[0] = 0x30;  tx_data[1] = 0x0B;

    iic.send(iic_cam_addr,tx_data,2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x40':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [47]:
def camera_system_clk(): 
    tx_data[0] = 0x31;  tx_data[1] = 0x03;
    tx_data[2] = 0x11

    iic.send(iic_cam_addr, tx_data, 3) 

In [48]:
def iic_tx(reg, val):
    tx_data[0] = (reg>>8) & (0xFF);
    tx_data[1] = reg & (0xFF);
    tx_data[2] = val
    
    iic.send(iic_cam_addr, tx_data, 3) 
    print("sent -> {} {} {}".format(hex(tx_data[0]),hex(tx_data[1]),hex(tx_data[2])))

In [49]:
def vdma_init(videomode):
    if vdma.readchannel.running: 
        vdma.readchannel.stop()

    vdma.readchannel.mode = videomode

Start Driver Steps

In [50]:
setup_i2c_switch()

In [51]:
detect_camera()

send complete
camera detected


In [52]:
videomode = VideoMode(1920,1080,24)
                      
vdma_init(videomode)  

In [53]:
demosaic_config(1920,1080)
gamma_config(1920, 1080)

0x81
0x81


In [60]:
%run pcam_cfg.ipynb
#camera_system_clk()
iic_tx(0x3008, 0x82)
sleep(1.0)

iic_tx(0x3008, 0x42)
setting_func(cfg_init)
#iic_tx(0x3008, 0x02)

#iic_tx(0x3008, 0x42)
setting_func(cfg_1080p_30fps)
#setting_func(cfg_720p_60fps)
#iic_tx(0x3008, 0x02)

#iic_tx(0x3008, 0x42)
setting_func(cfg_simple_awb)
iic_tx(0x3008, 0x02)

vdma.readchannel.start()

sent -> 0x30 0x8 0x82
sent -> 0x30 0x8 0x42
sent -> 0x30 0x8 0x2


In [ ]:
#vdma.readchannel.start()
frame = vdma.readchannel.readframe()

print(len(frame))
PIL.Image.fromarray(frame[:,:,[2,1,0]])

In [61]:
import time
num_frames = 20000000
start = time.time()

displayport = DisplayPort()
print(displayport)
displayport.configure(videomode, PIXEL_RGB)
print(displayport)
print(videomode)
for _ in range (num_frames):
    frame = displayport.newframe()
    frame[:] = vdma.readchannel.readframe()
    displayport.writeframe(frame)

end = time.time()
duration = end - start
print(f"Took {duration} seconds at {num_frames / duration} FPS")

VideoMode: width=1920 height=1080 bpp=24 fps=60


KeyboardInterrupt: 

In [ ]:
displayport.close()

vdma.readchannel.stop()

#base.free()